### End to End Project

### Dataset
    - The dataset used in this project is Amazon Kindle Store category between May 1996 to July 2014.
    - This data contains reviews of customers for Amazon Kindle.
    - Main columns in dataset
        - asin - ID of the product
        - overall - rating of the product
        - reviewText - text of the review
        - summary - summary of the review
        - reviewerID - ID of the reviewer

### Plan of Action
- Step 1) Data load
- Step 2) Feature Engineering - Text pre-processing(Lemmatization) and cleaning
- Step 3) Train Test Split
- Step 4) BOW, TF-IDF, Word2Vec
    - Convert Text based features (input features here) to Vectors (numerical format)
- Step 5) Train ML algorithms
- Step 6) Evaluate performance of the models





In [1]:
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
from bs4 import BeautifulSoup
import lxml
from nltk.stem import WordNetLemmatizer
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import confusion_matrix,accuracy_score,classification_report
import numpy as np
from gensim.models import Word2Vec
from gensim.utils import simple_preprocess
from tqdm import tqdm

[nltk_data] Error loading stopwords: <urlopen error [Errno 8] nodename
[nltk_data]     nor servname provided, or not known>


In [2]:
# Step 1) Load data
df = pd.read_csv('./resources/all_kindle_review.csv')
df.head()

Unnamed: 0.1  Unnamed: 0        asin  helpful  rating  \
0             0       11539  B0033UV8HI  [8, 10]       3   
1             1        5957  B002HJV4DE   [1, 1]       5   
2             2        9146  B002ZG96I4   [0, 0]       3   
3             3        7038  B002QHWOEU   [1, 3]       3   
4             4        1776  B001A06VJ8   [0, 1]       4   

                                          reviewText   reviewTime  \
0  Jace Rankin may be short, but he's nothing to ...   09 2, 2010   
1  Great short read.  I didn't want to put it dow...   10 8, 2013   
2  I'll start by saying this is the first of four...  04 11, 2014   
3  Aggie is Angela Lansbury who carries pocketboo...   07 5, 2014   
4  I did not expect this type of book to be in li...  12 31, 2012   

       reviewerID  reviewerName                   summary  unixReviewTime  
0  A3HHXRELK8BHQG        Ridley  Entertaining But Average      1283385600  
1  A2RGNZ0TRF578I  Holly Butler   Terrific menage scenes!      1381190400  
2  A3S0H2HV6U1I7F       Merissa          Snapdragon Alley      1397174400  
3   AC4OQW3GZ919J    Cleargrace    very light murder cozy      1404518400  
4  A3C9V987IQHOQD      Rjostler                      Book      1356912000

In [3]:
# Step 2) Feature Engineering

# Step 2.1)  Select relevant columns 
# x = input = reviewText
# y = output = rating
df=df[['reviewText','rating']]
print('df.shape = ',df.shape)
df.head()

df.shape =  (12000, 2)


reviewText  rating
0  Jace Rankin may be short, but he's nothing to ...       3
1  Great short read.  I didn't want to put it dow...       5
2  I'll start by saying this is the first of four...       3
3  Aggie is Angela Lansbury who carries pocketboo...       3
4  I did not expect this type of book to be in li...       4

In [4]:
# Step 2.2) Find null values in data
# Output observation: There are NO null values in both 'reviewText' and 'rating' columns
null_counts = df.isnull().sum()
print('Null values in each column:\n', null_counts)

Null values in each column:
 reviewText    0
rating        0
dtype: int64


In [5]:
# Step 2.3) Perform Feature Engineering > 'rating' column

# Step 2.3.1) Find unique values in output column 'rating'
# Output observation: The 'rating' column has 5 unique values - [1, 2, 3, 4, 5]
unique_ratings = df['rating'].unique()
print('Unique ratings in the dataset:', unique_ratings)

Unique ratings in the dataset: [3 5 4 2 1]


In [6]:
# Step 2.3.2) Find the distribution of ratings
# Output Observation: The dataset is NOT an imbalanced data spread across all 5 ratings.
rating_distribution = df['rating'].value_counts()
print('Rating distribution:\n', rating_distribution)

Rating distribution:
 rating
5    3000
4    3000
3    2000
2    2000
1    2000
Name: count, dtype: int64


In [7]:
# Step 2.3.3) Convert 'ratings' column into 0's and 1'
# - Current rating values: 1, 2, 3, 4, 5
# - New rating values: 0 (for ratings 1, 2), 1 (for ratings 3,4, 5)
# Output observation: The value_counts tells us that 
# - 1: 8000 count
# - 0: 7000 count
# Thus the dataset is NOT imbalanced.
df['rating'] = df['rating'].apply(lambda x: 0 if x < 3 else 1)
print('Unique ratings in the dataset:', df['rating'].unique())
print('df[rating].value_counts() = ',df['rating'].value_counts())
df.head(100)


Unique ratings in the dataset: [1 0]
df[rating].value_counts() =  rating
1    8000
0    4000
Name: count, dtype: int64


reviewText  rating
0   Jace Rankin may be short, but he's nothing to ...       1
1   Great short read.  I didn't want to put it dow...       1
2   I'll start by saying this is the first of four...       1
3   Aggie is Angela Lansbury who carries pocketboo...       1
4   I did not expect this type of book to be in li...       1
..                                                ...     ...
95  Gage Warren harbors a serious crush for the se...       1
96  Easy read and provided several very useful tip...       1
97  this book is an absolute waste. there are now ...       0
98  Because there really are very few good liberal...       1
99  Author and editors should do a better job of p...       1

[100 rows x 2 columns]

In [8]:
# Step 2.4) Perform Feature Engineering > 'reviewText' column

# Step 2.4.1) Lowercase all text in 'reviewText' column
df['reviewText'] = df['reviewText'].str.lower()

In [9]:
# Step 2.5) Remove Special Charaters from 'reviewText' column
df['reviewText']=df['reviewText'].apply(lambda x:re.sub('[^a-z A-z 0-9-]+', '',x))
## Remove the stopswords
df['reviewText']=df['reviewText'].apply(lambda x:" ".join([y for y in x.split() if y not in stopwords.words('english')]))
## Remove url 
df['reviewText']=df['reviewText'].apply(lambda x: re.sub(r'(http|https|ftp|ssh)://([\w_-]+(?:(?:\.[\w_-]+)+))([\w.,@?^=%&:/~+#-]*[\w@?^=%&/~+#-])?', '' , str(x)))
## Remove html tags
df['reviewText']=df['reviewText'].apply(lambda x: BeautifulSoup(x, 'lxml').get_text())
## Remove any additional spaces
df['reviewText']=df['reviewText'].apply(lambda x: " ".join(x.split()))

df.head()

reviewText  rating
0  jace rankin may short hes nothing mess man hau...       1
1  great short read didnt want put read one sitti...       1
2  ill start saying first four books wasnt expect...       1
3  aggie angela lansbury carries pocketbooks inst...       1
4  expect type book library pleased find price right       1

In [10]:
# Step 2.6) Lemmitization of 'reviewText' column 
lemmatizer=WordNetLemmatizer()

# Function to Lemmatize
def lemmatize_words(text):
    return " ".join([lemmatizer.lemmatize(word) for word in text.split()])

# Apply lemmatization
df['reviewText']=df['reviewText'].apply(lambda x:lemmatize_words(x))

df.head()

reviewText  rating
0  jace rankin may short he nothing mess man haul...       1
1  great short read didnt want put read one sitti...       1
2  ill start saying first four book wasnt expecti...       1
3  aggie angela lansbury carry pocketbook instead...       1
4  expect type book library pleased find price right       1

In [11]:
# Step 3) Train Test Split
# At this time:-
# - reviewText (input feature) has cleaned text data
# - rating (output feature) has 0's and 1's
x = df['reviewText']
y = df['rating']    
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)
print('X_train.shape = ',x_train.shape)
print('X_test.shape = ',x_test.shape)



X_train.shape =  (9600,)
X_test.shape =  (2400,)


In [12]:
# Step 4) Generate x_train and x_test for Bag of Words (BoW) Vectorization, TF-IDF Vectorization, Word2Vec Embedding

# Step 4.1) Bag of Words (BoW) Vectorization
bow=CountVectorizer()
x_train_bow=bow.fit_transform(x_train)
x_test_bow=bow.transform(x_test)

In [13]:
# Step 4.2) TF-IDF Vectorization
tfidf=TfidfVectorizer()
x_train_tfidf=tfidf.fit_transform(x_train)
x_test_tfidf=tfidf.transform(x_test)


In [14]:
# Step 4.3) Word2Vec Embedding

# Step 4.3.1) Tokenize train/test text into lists of words
# This step of simple_preprocess is optinoal as we have already cleaned the text data
x_train_cleaned = [simple_preprocess(str(text)) for text in x_train]
x_test_cleaned  = [simple_preprocess(str(text)) for text in x_test]

print('x_train_word2vec = ',x_train_cleaned)

# Step 4.3.2) Train a Word2Vec model on TRAIN tokens only (no data leakage)
w2v_model = Word2Vec(
    sentences=x_train_cleaned,
    vector_size=100,   # you can change to 300 if you want
    window=5,
    min_count=2,
    workers=4,
    sg=0               # 0 = CBOW, 1 = Skip-gram
)

EMB_DIM = w2v_model.wv.vector_size

# Step 4.3.3) Convert each document to a fixed-length vector by averaging word vectors
def doc_avg_w2v(tokens):
    vecs = [w2v_model.wv[w] for w in tokens if w in w2v_model.wv.key_to_index]
    if not vecs:
        return np.zeros(EMB_DIM, dtype=np.float32)
    return np.mean(vecs, axis=0).astype(np.float32)

# Step 4.3.4) Create document vectors for train and test sets
x_train_w2v = np.vstack([doc_avg_w2v(toks) for toks in tqdm(x_train_cleaned)])
x_test_w2v  = np.vstack([doc_avg_w2v(toks) for toks in tqdm(x_test_cleaned)])

print("x_train_w2v shape =", x_train_w2v.shape)
print("x_test_w2v shape  =", x_test_w2v.shape)

x_train_word2vec =  [['looking', 'forward', 'book', 'came', 'double', 'space', 'every', 'paragraph', 'kindle', 'edition', 'since', 'action', 'move', 'around', 'formatting', 'make', 'story', 'hard', 'follow', 'die', 'hard', 'like', 'want', 'botherits', 'sad', 'thing', 'good', 'book', 'spoiled', 'formatting', 'fault', 'author', 'story', 'good', 'book', 'energy', 'read', 'itive', 'also', 'emailed', 'author'], ['already', 'owned', 'book', 'spouse', 'forgot', 'already', 'part', 'library', 'book', 'unfortunate', 'amazon', 'safeguard', 'place', 'notify', 'book', 'already', 'library'], ['cool', 'forgot', 'request', 'rate', 'came', 'make', 'mine', 'unreliable', 'rating', 'doubt', 'change', 'rotation', 'planet', 'enough', 'measure'], ['short', 'short', 'story', 'basically', 'scene', 'party', 'one', 'night', 'though', 'admittedly', 'entire', 'book', 'taken', 'period', 'one', 'doesnt', 'pure', 'erotica', 'hea', 'real', 'relationship', 'depth', 'sexual', 'description', 'really', 'disappointed', 'ge

100%|██████████| 2400/2400 [00:00<00:00, 12430.48it/s]

x_train_w2v shape = (9600, 100)
x_test_w2v shape  = (2400, 100)


In [15]:
# Step 5) Train ML Models - Gaussian Naive Bayes 
# 3 Models will be trained: (1) BoW, (2) TF-IDF, (3) Word2Vec

# Step 5.1) Model 1: Gaussian Naive Bayes on BoW Vectors
ml_model_bow=GaussianNB().fit(x_train_bow.toarray(),y_train)

# Step 5.2) Model 2: Gaussian Naive Bayes on TF-IDF Vectors
ml_model_tfidf=GaussianNB().fit(x_train_tfidf.toarray(),y_train)

# Step 5.3) Model 3: Gaussian Naive Bayes on Word2Vec
ml_model_w2v=GaussianNB().fit(x_train_w2v,y_train)

In [16]:
# Step 6) Evaluate performance of all 3 models

# Step 6.1) Evaluate Model 1: Gaussian Naive Bayes on BoW Vectors
y_pred_bow=ml_model_bow.predict(x_test_bow.toarray())
print('--- Model 1: Gaussian Naive Bayes on BoW Vectors ---')
print('Confusion Matrix:\n',confusion_matrix(y_test,y_pred_bow))
print('Accuracy Score:',accuracy_score(y_test,y_pred_bow))
print('Classification Report:\n',classification_report(y_test,y_pred_bow))  

# Step 6.2) Evaluate Model 2: Gaussian Naive Bayes on TF-IDF Vectors
y_pred_tfidf=ml_model_tfidf.predict(x_test_tfidf.toarray())
print('--- Model 2: Gaussian Naive Bayes on TF-IDF Vectors ---')
print('Confusion Matrix:\n',confusion_matrix(y_test,y_pred_tfidf))
print('Accuracy Score:',accuracy_score(y_test,y_pred_tfidf))
print('Classification Report:\n',classification_report(y_test,y_pred_tfidf))    

# Step 6.3) Evaluate Model 3: Gaussian Naive Bayes on Word2Vec
y_pred_w2v=ml_model_w2v.predict(x_test_w2v)
print('--- Model 3: Gaussian Naive Bayes on Word2Vec ---')
print('Confusion Matrix:\n',confusion_matrix(y_test,y_pred_w2v))
print('Accuracy Score:',accuracy_score(y_test,y_pred_w2v))
print('Classification Report:\n',classification_report(y_test,y_pred_w2v))


--- Model 1: Gaussian Naive Bayes on BoW Vectors ---
Confusion Matrix:
 [[499 304]
 [717 880]]
Accuracy Score: 0.5745833333333333
Classification Report:
               precision    recall  f1-score   support

           0       0.41      0.62      0.49       803
           1       0.74      0.55      0.63      1597

    accuracy                           0.57      2400
   macro avg       0.58      0.59      0.56      2400
weighted avg       0.63      0.57      0.59      2400

--- Model 2: Gaussian Naive Bayes on TF-IDF Vectors ---
Confusion Matrix:
 [[488 315]
 [696 901]]
Accuracy Score: 0.57875
Classification Report:
               precision    recall  f1-score   support

           0       0.41      0.61      0.49       803
           1       0.74      0.56      0.64      1597

    accuracy                           0.58      2400
   macro avg       0.58      0.59      0.57      2400
weighted avg       0.63      0.58      0.59      2400

--- Model 3: Gaussian Naive Bayes on Word2Vec 